# Requirement

In [1]:
# !pip install requests beautifulsoup4 jieba 

In [2]:
import requests
from bs4 import BeautifulSoup
import jieba

from tracemalloc import start
from urllib import response
from itsdangerous import exc
import time
import json
import os
import platform

In [3]:
print("python version : " + platform.python_version())

python version : 3.9.13


# Comment Judge

In [4]:
# 去看哪一條評論最多讚
class CommentJudge():
    def getBest(self, comments):
        self.comments = comments
        self.segment_comments = []
        self.wordDict = {}
        self.commentsScore = []

        self.segment()
        self.buildWordDict()
        self.score()

        maxScore, maxIndex = 0, 0
        for index in range(len(self.commentsScore)):
            score = self.commentsScore[index]
            if score > maxScore:
                maxScore = score
                maxIndex = index
        return self.comments[maxIndex], self.commentsScore[maxIndex]
    
    def segment(self):
        banned = [' ', ',', '，', '。', '？', '?', '='] #過濾的字符
        for comment in self.comments:
            words = [ word for word in jieba.cut(comment) if word not in banned] # 用jieba做分詞
            self.segment_comments.append(words)

    def buildWordDict(self):
        for comment in self.segment_comments:
            for word in comment:
                if word in self.wordDict:
                    self.wordDict[word] += 1 #如果說是重複的詞+1
                else:
                    self.wordDict[word] = 0 #如果是新的則初始化為0
    
    def score(self):
        for index in range(len(self.segment_comments)):
            comment = self.segment_comments[index]
            if len(self.comments[index]) >= 15: #如果此評論超過15個字元，則是0分
                self.commentsScore.append(0)
                continue

            weight = 0
            for word in comment:
                weight += self.wordDict[word] # 根據jieba中的字典累加得分

            self.commentsScore.append(weight)

# Crawler

In [5]:
class PTTCrawler():
    def __init__(self, board, startURL='index.html'):
        self.board = board
        self.startURL = startURL
        self.judge = CommentJudge()
        if requests.get('https://www.ptt.cc/bbs/{}/index.html'.format(self.board)).status_code != 200:
            raise Exception("No board in PTT named {}".format(self.board))
    
    def getPosts(self, number=50000):
        url = 'https://www.ptt.cc/bbs/{}/{}'.format(self.board, self.startURL)
        
        if os.path.isfile('train.json'):
            with open('train.json') as fp:
                ans = json.load(fp)
                counter = len(ans)
        else:
            ans = []
            counter = 0

        while counter < number:
            print(url)
            response = requests.get(url, headers={'cookie': 'over18=1;'})
            if response.status_code == 200:
                # 取得文章的標題和URL，並進一步 call getComments() 取得推文
                root = BeautifulSoup(response.text, 'html.parser')
                posts = root.find_all('div', class_='r-ent')
                for post in posts:
                    link = post.find("a")
                    if link:                        # 如果被刪文，則會是 Noneor "[閒聊]"[問題]
                        if  "[問題]" in link.text and "Re:" not in link.text:
                            counter += 1

                            comments = self.getComments(link.get('href'))
                            if len(comments) != 0:
                                bestComment, score = self.judge.getBest(comments)
                                ans.append({
                                    "Q": link.text.replace('[問題]', ''),
                                    "A": bestComment
                                })
                                print(ans[-1], counter)
                                time.sleep(2.5)
                                if counter % 100 == 0:
                                    with open('train.json', 'w') as fp:
                                        json.dump(ans, fp)
                        if  "[閒聊]" in link.text and "Re:" not in link.text:
                            counter += 1

                            comments = self.getComments(link.get('href'))
                            if len(comments) != 0:
                                bestComment, score = self.judge.getBest(comments)
                                ans.append({
                                    "Q": link.text.replace('[閒聊]', ''),
                                    "A": bestComment
                                })
                                print(ans[-1], counter)
                                time.sleep(2.5)
                                if counter % 100 == 0:
                                    with open('train.json', 'w') as fp:
                                        json.dump(ans, fp)
                
                # 取得上一頁的位址
                btns = root.find_all('a', class_='btn wide')
                for btn in btns:
                    if '上頁' in btn.text:
                        url = 'https://www.ptt.cc{}'.format(btn.get('href'))
                        print(url)
                        print()
                # time.sleep(3)
            else:
                raise Exception("Response status code {}".format(response.status_code))
        return ans
    #取得評論
    def getComments(self, url):
        url = 'https://www.ptt.cc{}'.format(url)
        ans = []
        response = requests.get(url, headers={'cookie': 'over18=1;'})
        root = BeautifulSoup(response.text, 'html.parser')
        comments = root.find_all('div', class_='push')
        for comment in comments:
            try:
                text = comment.find_all('span')[2].text
                if 'http' not in text:
                    ans.append(text.replace(': ', ''))
            except:
                print(comment)  # 推文太多會出現 error
        return ans

In [6]:
# https://www.ptt.cc/bbs/C_Chat/index.html
crawler = PTTCrawler("C_Chat", 'index17650.html')
posts = crawler.getPosts()

https://www.ptt.cc/bbs/C_Chat/index17650.html


Building prefix dict from the default dictionary ...
Loading model from cache C:\Users\WORKSP~1\AppData\Local\Temp\jieba.cache
Loading model cost 0.588 seconds.
Prefix dict has been built successfully.


{'Q': ' 統神吃拉麵打翻會跟老闆怎樣', 'A': '會被老闆肛'} 1
{'Q': ' battle.net台灣被限速？', 'A': '就改了位置,改版又改回去了'} 2
{'Q': ' 黑川露比帽子誰才是我推第一女主角？', 'A': '照理來說 是露比 照理來說啦'} 3
{'Q': ' 命理師會怎麼評價人魚小美的長相', 'A': '對自己的命運看得很開'} 4
{'Q': '作者再推「柯哀」CP？青山剛昌手繪賀圖', 'A': '嘔嘔嘔嘔嘔嘔'} 5
{'Q': ' 蜘蛛人請統神配音會怎樣', 'A': '哇，他的手可以穿過我的蜘蛛網'} 6
{'Q': ' 薩爾達先玩王淚再玩曠野會怎樣？', 'A': '欸我的轟炸機呢？我的鋼彈呢？'} 7
{'Q': ' 市川會怎麼跟山田談場Lv999的戀愛?', 'A': '甲下'} 8
{'Q': ' 芸芸這個滑接 可以簽約了吧', 'A': '接住了'} 9
{'Q': ' 看了時下最火紅的百合動畫 神無月的巫女', 'A': '大神的雙翼直接飛走的詭異作品'} 10
{'Q': ' 血色降臨又是一款變魔術失敗的遊戲', 'A': '傑森又要多什麼稱號了嗎'} 11
https://www.ptt.cc/bbs/C_Chat/index17649.html

https://www.ptt.cc/bbs/C_Chat/index17649.html
{'Q': ' 為何我推第七集觀看數比3～6集高啊', 'A': '吹的那麼神再來說驟降很正常'} 12
{'Q': '利瓦爾擅自問魯路修有導致學園被封殺嗎', 'A': '他是記者嗎'} 13
{'Q': ' 特級廚師考題如果出的是「拉麵非拉麵」', 'A': '沾麵冷麵擔擔麵頂上'} 14
{'Q': ' 哇靠 我得到一台WiiU耶！', 'A': '除了XBX全都移植了'} 15
{'Q': ' 請拉麵職人當特級廚師考試評審會怎樣？', 'A': '煮石頭水的先轟出去'} 16
{'Q': ' 如果黑川茜吃拉麵太燙會怎樣', 'A': '愛會把舌頭吐出來吃麵'} 17
{'Q': ' 魔法咪路咪路一日復活連載', 'A': '惡魯莫德的個人回都很可愛'} 18
{'Q': ' 土方十四吃拉麵會被趕出來嗎？', 'A': '他可能會被老闆扁'} 20
{'

{'Q': ' 大家還記得齊木楠雄嗎？', 'A': '超好看，心目中前幾名的搞笑番'} 138
{'Q': ' 警察也知道米花市治安不好喔？', 'A': '齁齁做逮記'} 139
{'Q': ' 喝小當家寶山飛龍鍋加冰水會怎樣', 'A': '李嚴:要加就加毒針'} 140
{'Q': ' 不道德公會 前面幾集也太難買', 'A': '哈哈 我買走的啦'} 141
{'Q': '中川翔子頻收死亡威脅\u3000推特感嘆：每次報', 'A': '落井下石的人是有病嗎'} 142
{'Q': ' 女朋友被金毛帶走', 'A': '蛤'} 143
{'Q': ' 吃大亨堡', 'A': 'OP囉'} 144
{'Q': ' 必定能殺掉探險者的地城', 'A': '沒研磨劑水刀沒那麼威吧'} 145
{'Q': ' switch 現在的螢幕夠大嗎？', 'A': '你手機多大? 你玩手遊嗎'} 146
https://www.ptt.cc/bbs/C_Chat/index17632.html

https://www.ptt.cc/bbs/C_Chat/index17632.html
{'Q': ' 台灣線上遊戲的伺服器怎那麼爛', 'A': '西台灣蝗蟲大舉入侵阿是載的完'} 147
{'Q': ' 超粒方評小美人魚', 'A': '知名啊，哪種方面的不好說'} 148
{'Q': ' 說出真相卻被眾人當作說謊時會是甚麼感覺', 'A': '跟秀哥道歉'} 149
{'Q': ' 虎鯨會不會是反串仔樂子人= =', 'A': '我推都有演 偶像就是要會騙人'} 150
{'Q': ' Jump shop沒預購的非熱門商品販售問題', 'A': '不確定了'} 151
{'Q': ' 冠茂的實力可以把摩納哥杯車過去嗎?', 'A': '他有很愛麵包嗎'} 152
{'Q': ' 黑川是處女是勝過星野愛最多的地方？', 'A': '為了模仿愛就不是了吧？'} 153
{'Q': ' 當年承太郎這個判斷法ok嗎', 'A': '就當然是.....'} 154
{'Q': ' 我覺得霍爾最帥得時候是做早餐的時候', 'A': '看起來真的好吃，我是說培根蛋'} 155
{'Q': ' 求乙女+鳳凰傲+魔法 轉生役世界漫畫', 'A': '魔法學院的 劇情向 前面小虐'} 15

{'Q': ' 小美人魚可以拿幾座奧斯卡?', 'A': '保底最佳女主跟最佳劇本'} 278
{'Q': ' master duel很農嗎', 'A': '的是前幾樓提到的環境臭'} 279
{'Q': '想省錢？Konami《潛龍諜影 Delta：食蛇者', 'A': '有魔獸蟲蛀的味道出來了'} 280
{'Q': ' 這種動畫畫風怎麼消失了', 'A': '是的，你的感受偏小眾'} 281
{'Q': ' 哆啦A夢是不是又有道具要實現了？', 'A': '那就算是要取代了吧'} 282
{'Q': ' 王國之淚快速煮獸肉的方法', 'A': '你都要複製了還在吃獸肉=='} 283
{'Q': ' 你還願意給暴雪一次機會玩暗黑破壞神4嗎', 'A': '我要是玩了我就是小狗'} 284
{'Q': ' 鈴木愛理唱《創聖のアクエリオン》好聽', 'A': '何止偶像 是偶像的偶像'} 285
{'Q': ' 這次王國之淚的劇情還不錯吧(有雷', 'A': '散沒代入感的聲音'} 286
https://www.ptt.cc/bbs/C_Chat/index17615.html

https://www.ptt.cc/bbs/C_Chat/index17615.html
{'Q': ' 如果童話王國出真人版會怎麼演？', 'A': '這個真的很讚'} 287
{'Q': ' 體驗軍旅生活的遊戲', 'A': '台灣比較爛的是刺槍術'} 288
{'Q': ' 等我成長到能贏過妳之後，就嫁給我吧!', 'A': '那女的頭上有角 應該是鬼'} 289
{'Q': ' Ina突然發現了殘酷的現實...XD', 'A': '我婆們可愛wah'} 290
{'Q': ' FF14製作組在新BOSS戰加了天眼視角梗', 'A': '笑死 用外掛的會不會變更遠'} 291
{'Q': ' 王國之淚會3D暈嗎', 'A': '一直狂轉視角就會，但通常不會'} 292
https://www.ptt.cc/bbs/C_Chat/index17614.html

https://www.ptt.cc/bbs/C_Chat/index17614.html
{'Q': ' 要先當海利亞人還是涅法雷姆？', 'A': '有朋友一起玩可以玩D4'} 293
{'Q': ' TCG卡牌在台

...

{'Q': ' 現在7.1聲道耳機有比較進步嗎？', 'A': '鄰居的投訴也會讓你很感動'} 49465
{'Q': ' 奇幻自衛隊的gate開在中國會怎樣', 'A': '你的歷史課不是我的歷史課'} 49466
{'Q': ' 影之強者04 阿爾法也太婆了吧 ==', 'A': '哭啊 真不愧是暗影大人'} 49467
{'Q': ' 瘟疫公司全員感染，致死率超低算輸嗎？', 'A': '難度提高醫生是一定會發現的'} 49468
{'Q': ' 日本八卦雜誌披露2022年紅白候補名單', 'A': 'Ado能上不意外好嗎'} 49469
{'Q': ' 法環 蒙格特 知道 他弟蒙格 幹得鳥是嗎', 'A': '知道吧 他把所有人罵過一遍'} 49470
{'Q': ' 低彩度的畫風怎麼分辨？', 'A': '白色偏過去的顏色，彩度就愈低'} 49471
{'Q': ' 大家最期待哪部Jump漫畫動畫化?', 'A': 'act-age早涼了吧'} 49472
https://www.ptt.cc/bbs/C_Chat/index11755.html

https://www.ptt.cc/bbs/C_Chat/index11755.html
{'Q': ' 白貓高爾夫', 'A': '技能總會越出越強'} 49473
{'Q': ' 醫生遇到巨乳如何聽診?', 'A': '我的家庭醫生看女的只聽背部'} 49474
{'Q': ' 小孤獨容易中催眠嗎？', 'A': '你是快了還是慢了'} 49475
{'Q': ' 暗影大人老了會禿頭嗎', 'A': '以髮色看媽媽基因好像強一點'} 49476
{'Q': ' 原神草神PV 末端符文翻譯', 'A': '是他不想去干涉賢者 不是沒空'} 49477
{'Q': ' 換種田要立旗了嗎？', 'A': '對不起 是我'} 49478
{'Q': ' 還有哪家公司適合做鏈鋸人？', 'A': '超厚的公司 完全不輸給一線的'} 49479
https://www.ptt.cc/bbs/C_Chat/index11754.html

https://www.ptt.cc/bbs/C_Chat/index11754.html
{'Q': ' 影之強者 遊戲角色介紹 ', 'A': '我還以為跟著動畫一起出'} 49

{'Q': '《蓓優妮塔3》團隊：任天堂之恩永世難忘！', 'A': '就說是任天堂救了這系列了'} 49599
{'Q': ' 原神為啥到現在NPC還是都用共用模組?', 'A': '就連你玩的角色也是共用模組'} 49600
{'Q': ' 男生會喜歡的男聲優有誰?', 'A': '若本、子安、諏訪部'} 49601
{'Q': ' Echo團突破絕龍詩戰爭P6 迎擊騎神最終型態', 'A': '原來他們還有在打絕龍= ='} 49602
{'Q': ' 水星魔女有可能超越當年SEED的人氣嗎', 'A': '拿前三集的推量來比不就知道了'} 49603
{'Q': ' 考哥只是詮釋了他的角色啊', 'A': '只好回你 考哥.jpg 了'} 49604
https://www.ptt.cc/bbs/C_Chat/index11740.html

https://www.ptt.cc/bbs/C_Chat/index11740.html
{'Q': ' 水星上有備長炭嗎？', 'A': '問麥特戴蒙啊'} 49605
{'Q': ' 英雄最適合搭配的動漫是銀魂嗎？', 'A': '馬上就想到這個www'} 49606
{'Q': ' 棒球大聯盟2nd 連載再開之作者留言', 'A': '高中就變壘球大聯盟惹'} 49607
{'Q': ' 有沒有頭髮遮住眼睛的角色', 'A': '現在的我看不到未來.jpg'} 49608
{'Q': ' 明年初的光榮特庫摩 是火力展示還是撞爛', 'A': '是我查資料的時候眼幹'} 49609
{'Q': ' 鬥陣特攻做動畫能演甚麼?', 'A': '官方的短片就很讚了'} 49610
{'Q': ' 櫻井孝宏比台灣演藝知名案例還過分吧', 'A': '在一起的都知道他是派對動物'} 49611
{'Q': ' 水星魔女  横槍メンゴ畫的蘇萊塔', 'A': '雀丘你的扳手收起來啊（怕'} 49612
{'Q': ' 死神的劇情是不是播的剛剛好', 'A': '笑死 先知'} 49613
https://www.ptt.cc/bbs/C_Chat/index11739.html

https://www.ptt.cc/bbs/C_Chat/index11739.html
{'Q': ' 小綠是卑在哪裡啊', 'A': '因為

{'Q': ' 強強劍是不是真的強強', 'A': '無敵的吧'} 49731
{'Q': ' 新竹米粉算是麵非麵嗎？', 'A': '難的是還要有麵的口感'} 49732
{'Q': ' 異形有什麽科學價值', 'A': '強的基因的價值是很高的'} 49733
{'Q': ' 鑽石王牌推特', 'A': '不喔 春甲沒幾話就結束了'} 49734
{'Q': ' 鑽石王牌之前的劇情也差不多算完結了吧', 'A': '現在只剩下噗哈哈哈哈哈哈哈哈'} 49735
{'Q': ' 比較喜歡追番還是一口氣看完？', 'A': '劇情番一次看完 日常番慢慢追'} 49736
https://www.ptt.cc/bbs/C_Chat/index11725.html

https://www.ptt.cc/bbs/C_Chat/index11725.html
{'Q': ' 客家人是不是真的很厲害?', 'A': '太平天國王者'} 49737
{'Q': ' ↓雙葉在這裡', 'A': '還以為雙葉被擠到下一串...'} 49738
{'Q': ' 異世界迷宮的後宮生活 BD發售特典', 'A': '動畫未收錄影片...床戲?'} 49739
{'Q': ' 滿田怎麼不畫泉美跟大吾在同個時期打球', 'A': '爸媽的優良基因都被她繼承走了'} 49740
{'Q': ' 井之頭五郎來新竹吃東西會有啥反應?', 'A': '好難吃(嚼嚼) 好貴(嚼嚼)'} 49741
{'Q': ' 水星魔女  我想變成小鳥', 'A': '米米屁股好ㄔ……我是說好色'} 49742
{'Q': ' 轉生史萊姆 101 宴會結束', 'A': '這部的本體就是慶典和宴會啊'} 49743
https://www.ptt.cc/bbs/C_Chat/index11724.html

https://www.ptt.cc/bbs/C_Chat/index11724.html
{'Q': ' 萬代推出可以現金或無現金支付的扭蛋機', 'A': '很恐怖的東西'} 49744
{'Q': ' 王牌投手 鑽石王牌 棒球大聯盟 都幾？', 'A': '王牌投手的大奶教練'} 49745
{'Q': ' Lycoris Recoil 莉可麗絲 BD第二卷開箱', 'A': '推！'} 49746
{

{'Q': ' memento mori到底在玩什麼？？？', 'A': '玩找BUG'} 49867
{'Q': ' 當初柱間要說什麼斑才願意留下？', 'A': '留下來或我跟你走'} 49868
{'Q': ' 小孤獨看到平澤唯會怎麼想?', 'A': '看唯和看小喜多有什麼差嗎？'} 49869
{'Q': ' 鋼彈歌曲文藝復興了嗎？', 'A': '這首超紅的'} 49870
{'Q': '中古世紀類型遊戲的「豬」都做錯了！？荷', 'A': '天國降臨的豬就滿符合事實的'} 49871
{'Q': ' 小時候會看拉姆色色嗎？>///<', 'A': '幹 忘了看ID'} 49872
{'Q': ' 阿夸遊戲好香', 'A': '好可愛'} 49873
{'Q': 'hololive第5人！好狐白上吹雪訂閱數突破20', 'A': '媽的 色狐'} 49874
https://www.ptt.cc/bbs/C_Chat/index11710.html

https://www.ptt.cc/bbs/C_Chat/index11710.html
{'Q': ' 模型要組起來後才發現哪些沒上色嗎？', 'A': '色的了'} 49875
{'Q': ' 蔚藍檔案的體育服底下', 'A': '奶子!!!!'} 49876
{'Q': ' 鳴人出生時請雷影護衛會如何', 'A': '鳴人額頭會有一道雷電的胎記'} 49877
{'Q': ' 惡月十三 出大事了', 'A': '來不及了，開服紅利期已經過了'} 49878
{'Q': ' 今天是犬夜叉OP1發布22周年唷', 'A': '2000年  沒很久阿'} 49879
{'Q': '美國遊戲市場9月總體下降 PS5帶動硬體銷售', 'A': '贏過PS5'} 49880
{'Q': ' 原神插畫集 Vol.1 延後發售', 'A': '崩3零食箱是找郵局寄'} 49881
{'Q': ' 為什麼異世界不流行戴眼鏡的聰明胖子?', 'A': '胖子看起來都超廢的, 強在哪'} 49882
{'Q': ' 間諜++9根本不適合小孩子看吧', 'A': '鬼滅小孩都能看了'} 49883
{'Q': ' AI繪圖閒聊。', 'A': '我好像有看過類似血條的東西。'} 49884
{'Q': ' 我拼完風靈鋼彈了

{'Q': ' 三橋廉跟小孤獨誰比較社恐', 'A': '三橋沒那麼怕人'} 50000
{'Q': ' 二次元審美 是什麼時候變成肥婆信仰的', 'A': '就廢文ID 不用跟他認真'} 50001
{'Q': ' 西魯曾經救過地球一次?', 'A': '不認識。我是看賽魯長大的'} 50002
{'Q': ' 存在深深的腦海裡的作品多嗎？', 'A': '我的心裡'} 50003
{'Q': ' 現實遇過“以為大家都要追她“的女生嗎', 'A': '她那樣講不是因為對自己有自信吧'} 50004
{'Q': ' 烙印勇士漫畫要不要追完?', 'A': '就看你自己了'} 50005
{'Q': ' 水星魔女  地球宿舍的飼養家畜', 'A': '米米的寵物跑出來了呢'} 50006
{'Q': ' 有躺平族主角嗎', 'A': '一護，直接變地毯'} 50007
{'Q': ' 蘿莉BBA很受歡迎 那BBA蘿莉呢?', 'A': '阿不就現實的老害嗎'} 50008
{'Q': ' 米津玄師 KICK BACK MV?晚上首播', 'A': '超過動畫版長度的後面很難聽'} 50009
https://www.ptt.cc/bbs/C_Chat/index11694.html



In [9]:
#從json轉成txt
def json2txt(file):
    name = file.split(".")[0]  #取得檔名
    with open(file, 'r', encoding='utf-8') as json_file:
        json_data = json.load(json_file)
    
    text_data = ''
    for item in json_data:
        text_data += f"Q: {item['Q']}\n"
        text_data += f"A: {item['A']}\n\n"

    with open('{}.txt'.format(name), 'w', encoding='utf-8') as txt_file:
        txt_file.write(text_data)

In [8]:
json2txt('train.json')